# module

In [25]:
import numpy as np
import hdbscan
from sklearn.datasets import make_blobs
from scipy.cluster.hierarchy import dendrogram
import plotly.graph_objects as go

def _get_leaves(condensed_tree):
    cluster_tree = condensed_tree[condensed_tree['child_size'] > 1]
    print(len(cluster_tree))
    if cluster_tree.shape[0] == 0:
        # Return the only cluster, the root
        return [condensed_tree['parent'].min()]

    root = cluster_tree['parent'].min()
    return _recurse_leaf_dfs(cluster_tree, root)
  
def _recurse_leaf_dfs(cluster_tree, current_node):
  children = cluster_tree[cluster_tree['parent'] == current_node]['child']
  if len(children) == 0:
      return [current_node,]
  else:
      return sum([_recurse_leaf_dfs(cluster_tree, child) for child in children], [])
  
def get_leaves(cluster_tree):
    """
    cluster_tree: (u, v, lambda_val, child_size, parent)
    """
    root = cluster_tree[:, 2].max()
    print(f"root: {root}")
    return recurse_leaf_dfs(cluster_tree, root)
    

def recurse_leaf_dfs(cluster_tree, current_node):
    # print(f"Visiting Node: {current_node}")
    child1 = cluster_tree[cluster_tree[:,2] == current_node][:,0]
    child2 = cluster_tree[cluster_tree[:,2] == current_node][:,1]
    # print(f"Children of Node {current_node}: Child1 {child1}, Child2 {child2}")

    if len(child1) == 0 and len(child2) == 0:
        
        return [current_node,]
    else:
        return sum([recurse_leaf_dfs(cluster_tree, child) for child in np.concatenate((child1, child2))], [])
    


def get_linkage_matrix_from_hdbscan(condensed_tree):
    """
    (child1, child2, parent, lambda_val, count)
    """
    linkage_matrix = []
    raw_tree = condensed_tree._raw_tree
    condensed_tree = condensed_tree.to_pandas()
    cluster_tree = condensed_tree[condensed_tree['child_size'] > 1]
    sorted_condensed_tree = cluster_tree.sort_values(by=['lambda_val','parent'], ascending=True)
    print(f"len of sorted condensed tree: {len(sorted_condensed_tree)}")

    for i in range(0, len(sorted_condensed_tree), 2):
    
        # 偶数行（i）と次の奇数行（i+1）をペアとして取得
        if i + 1 < len(sorted_condensed_tree):
            
            row_a = sorted_condensed_tree.iloc[i]
            row_b = sorted_condensed_tree.iloc[i+1]
            
            # **前提チェック**: lambda_valが同じであることを確認
            if row_a['lambda_val'] != row_b['lambda_val']:
                # lambda_valが異なる場合は、次の処理に進む（結合の前提が崩れる）
                raise ValueError(f"Lambda value mismatch at rows {i} and {i+1}: {row_a['lambda_val']} vs {row_b['lambda_val']}")
                
            # Parent IDが同じであることを確認 (同じ結合の結果である可能性が高い)
            if row_a['parent'] != row_b['parent']:
                # Parent IDが異なる場合は、このペアは単一の結合ではない可能性が高い
                raise ValueError(f"Parent ID mismatch at rows {i} and {i+1}: {row_a['parent']} vs {row_b['parent']}")
            
            child_a = row_a['child']
            child_b = row_b['child']
            lam = row_a['lambda_val']
            
            # count (サイズ) は、結合された2つの子ノードのサイズ合計を使うのが論理的だが、
            # HDBSCANは親ノードのサイズをリストで持っているため、ここではそのサイズを使用
            # より正確には、このParent IDを持つ全子ノードのサイズの合計を使うべきだが、
            # 2行の child_size の合計で暫定的に対応
            # total_size = row_a['child_size'] + row_b['child_size']


            total_size = raw_tree[raw_tree['child'] == row_a['parent']]['child_size']
            if len(total_size) == 0:
                total_size = row_a['child_size'] + row_b['child_size']
            else:
                total_size = total_size[0]
            # print(total_size)
            parent_id = row_a['parent']

            linkage_matrix.append([
                int(child_a), 
                int(child_b), 
                int(parent_id),
                lam, 
                total_size,
        ])   
    print(f"len of linkage matrix: {len(linkage_matrix)}")


    # 葉ノードに0-N-1のIDを振る
    node_id_map = {}
    current_id = 0
    leaves = _get_leaves(raw_tree)
    print(f"Number of leaves: {len(leaves)}")

    for leaf in leaves:
        node_id_map[int(leaf)] = current_id
        current_id += 1

    print(f"Leaf ID Map Size: {len(node_id_map)}")
    print(f"current id: {current_id}")

    # 結合ノードにIDを振る(linkage matrixのparent)
    for row in linkage_matrix.__reversed__():
        parent_id = row[2]
        if parent_id not in node_id_map:
            node_id_map[parent_id] = current_id
            current_id += 1

        else:
            print(f"Duplicate Parent ID found: {parent_id}")
            raise ValueError(f"Node ID {parent_id} already assigned!")
    print(f"Total Node ID Map Size: {len(node_id_map)}")
    print(f"current_id: {current_id}")

    # linkage matrixを書き換え
    max_lambda = max(row[3] for row in linkage_matrix)
    print(f"Max Lambda: {max_lambda}")
    linkage_matrix_mapped = [ 
        [node_id_map[row[0]], node_id_map[row[1]], node_id_map[row[2]], max_lambda - row[3], row[4]] 
        for row in linkage_matrix.__reversed__()
    ]

    return np.array(linkage_matrix_mapped), node_id_map

Y_CUTOFF = 0.5
def get_dendrogram_segments(Z: np.ndarray):
    """
    Linkage Matrixからデンドログラム描画に必要な座標データを取得します。
    """
    # 実際には可視化しないが、座標計算のために呼び出す
    # no_plot=True を指定すると、描画はスキップされる
    dendro_data = dendrogram(Z, no_plot=True, distance_sort='descending', count_sort='descending')
    
    # 'icoord': 各結合の水平方向の座標 (x座標)
    # 'dcoord': 各結合の垂直方向の座標 (y座標、結合距離)
    # これらは描画するV字/逆U字のセグメントを定義します。
    
    segments = []
    
    # icoord, dcoord は (4, K) の配列で、Kは結合の数 (N-1)
    # 各 i は (x1, x2, x3, x4) の座標リスト
    for icoords, dcoords in zip(dendro_data['icoord'], dendro_data['dcoord']):
        # (x1, y1), (x2, y2), (x3, y3), (x4, y4) がセグメントの頂点
        x1, x2, x3, x4 = icoords
        y1, y2, y3, y4 = dcoords

        if y1 == 0:
            if y4 == 0:
                new_y1 = y2
                new_y4 = y3
                new_x2 = (x2 + x3) / 2 + (x2 - x3) * 0.01
                new_x3 = (x2 + x3) / 2
            else:
                new_y1 = y2
                new_y4 = y4
                new_x2 = (x2 + x3) / 2
                new_x3 = x3
        else:
            if y4 == 0:
                new_y1 = y1
                new_y4 = y3
                new_x2 = x2
                new_x3 = (x2 + x3) / 2
            else:
                new_y1 = y1
                new_y4 = y4
                new_x2 = x2
                new_x3 = x3
        # if y1 == 0:
        #     y1 = y2
        #     new_x2 = (x2 + x3) / 2
        # if y4 == 0:
        #     y4 = y3
        #     new_x3 = (x2 + x3) / 2
        # if y1 !=0 and y4 !=0:
        #     new_x2 = x2
        #     new_x3 = x3
        

        # y1 = max(y1, Y_CUTOFF)
        # y4 = max(y4, Y_CUTOFF)
        # 1. 垂直線 (左の子ノードから結合点まで)
        segments.append([(x1, new_y1), (x2, y2)]) 
        # 2. 水平線 (結合したノード間)
        segments.append([(new_x2, y2), (new_x3, y3)]) 
        # 3. 垂直線 (右の子ノードから結合点まで)
        segments.append([(x4, new_y4), (x3, y3)]) 
    
    # segments は [[[x_start, y_start], [x_end, y_end]], ...] のリストになる
    return segments


def get_dendrogram_segments2(Z: np.ndarray):
    """
    Linkage Matrixからデンドログラム描画に必要な座標データを取得します。
    """
    # 実際には可視化しないが、座標計算のために呼び出す
    # no_plot=True を指定すると、描画はスキップされる
    dendro_data = dendrogram(Z, no_plot=True)
    
    # 'icoord': 各結合の水平方向の座標 (x座標)
    # 'dcoord': 各結合の垂直方向の座標 (y座標、結合距離)
    # これらは描画するV字/逆U字のセグメントを定義します。
    
    segments = []
    
    # icoord, dcoord は (4, K) の配列で、Kは結合の数 (N-1)
    # 各 i は (x1, x2, x3, x4) の座標リスト
    for icoords, dcoords in zip(dendro_data['icoord'], dendro_data['dcoord']):
        # (x1, y1), (x2, y2), (x3, y3), (x4, y4) がセグメントの頂点
        x1, x2, x3, x4 = icoords
        y1, y2, y3, y4 = dcoords

    
        if y1 == 0:
            y1 = y2
            new_x2 = (x2 + x3) / 2
        if y4 == 0:
            y4 = y3
            new_x3 = (x2 + x3) / 2
        if y1 !=0 and y4 !=0:
            new_x2 = x2
            new_x3 = x3
        

        # y1 = max(y1, Y_CUTOFF)
        # y4 = max(y4, Y_CUTOFF)
        # 1. 垂直線 (左の子ノードから結合点まで)
        segments.append([(x1, y1), (x2, y2)]) 
        # 2. 水平線 (結合したノード間)
        segments.append([(new_x2, y2), (new_x3, y3)]) 
        # 3. 垂直線 (右の子ノードから結合点まで)
        segments.append([(x4, y4), (x3, y3)]) 
    
    # segments は [[[x_start, y_start], [x_end, y_end]], ...] のリストになる
    return segments
def plot_dendrogram_plotly(segments, colors=None, scores=None):
    fig = go.Figure()
    
    for i, seg in enumerate(segments):
        # seg は [[x_start, y_start], [x_end, y_end]]
        x_coords = [seg[0][0], seg[1][0]]
        y_coords = [seg[0][1], seg[1][1]]
        
        color = 'blue' if colors is None else colors[i]
        info = "no" if scores is None else f"{scores[i]:.2f}"
        fig.add_trace(go.Scatter(
            x=x_coords, 
            y=y_coords, 
            mode='lines',
            line=dict(color=color, width=1),
            # showlegend=True,
            hoverinfo='text',
            text=f'Segment {i}: ({x_coords[0]:.2f}, {y_coords[0]:.2f}) to ({x_coords[1]:.2f}, {y_coords[1]:.2f}, score={info})'
        ))
    
    fig.update_layout(
        title='Simple Dendrogram Visualization',
        xaxis_title='Observation Index',
        yaxis_title='Distance / Height',
        hovermode='closest',
        
    )
    # fig.show() # 実行環境によっては直接表示
    
    # 葉ノードに名前を付ける場合は、dendrogram_data['leaves']と葉のy=0の座標を計算する必要があります。
    fig.update_layout(height=800, width=1000)
    # fig.update_traces(line =dict(color=colors, width=0.5))
    return fig

def calculate_strahler(Z_matrix: np.ndarray, n_leaves: int) -> np.ndarray:
    """
    Linkage Matrix (Z) に基づいて、各結合ノードのストラー数（Strahler Number）を計算する。
    
    Args:
        Z_matrix: Linkage Matrix (N-1 x 4のNumPy配列)。
        n_leaves: 元の観測値/葉ノードの数。
        
    Returns:
        np.ndarray: 各結合ノード（Zの各行）に対応するストラー数の配列。
    """
    n_merges = Z_matrix.shape[0]
    
    # 葉ノードのストラー数を初期化 (すべての葉ノードは S=1)
    # インデックス: 0から n_leaves - 1
    strahler_map = {i: 1 for i in range(n_leaves)}
    
    # Zの各行に対応するストラー数を格納するリスト
    merge_strahler_numbers = np.zeros(n_merges, dtype=int)
    
    # Z行列をボトムアップ（行 0 から N-2）で処理
    for i in range(n_merges):
        u_idx = int(Z_matrix[i, 0])  # 結合されるノード u
        v_idx = int(Z_matrix[i, 1])  # 結合されるノード v
        new_idx = n_leaves + i       # 新しく生成されるノード
        
        # 子ノードのストラー数を取得
        s_u = strahler_map.get(u_idx, 1)
        s_v = strahler_map.get(v_idx, 1)
        
        # ストラー数計算ロジック（二分木）
        if s_u == s_v:
            # S_u = S_v の場合、新しいノードのストラー数は S_u + 1
            s_new = s_u + 1
        else:
            # S_u != S_v の場合、新しいノードのストラー数は Max(S_u, S_v)
            s_new = max(s_u, s_v)
        
        # 結果を記録し、マップを更新
        merge_strahler_numbers[i] = s_new
        strahler_map[new_idx] = s_new

    return merge_strahler_numbers

def filter_linkage_matrix_by_strahler(Z_matrix: np.ndarray, S_min: int, N_leaves: int) -> np.ndarray:
    """
    Linkage Matrix (Z) にストラー数 (Strahler Number) を計算し、指定された最小ストラー数以上の結合のみを保持する。
    
    Args:
        Z_matrix (np.ndarray): Linkage Matrix (N-1 x 4)。
        S_min (int): フィルタリングのための最小ストラー数。

    Returns:
        np.ndarray: フィルタリングされたLinkage Matrix。
    """
    # 葉ノード数 (N_obs = Z.shape[0] + 1)
    # N_leaves = len(leaves) 

    # 1. ストラー数 (Strahler Number) の計算
    strahler_numbers = calculate_strahler(Z_matrix, N_leaves)

    # 2. Z_matrix の拡張 (ストラー数を5列目に追加)
    # (u, v, distance, count, strahler)
    Z_with_strahler = np.hstack((Z_matrix, strahler_numbers[:, np.newaxis]))

    # 3. フィルタリングの実行 (例: ストラー数 2 以上)
    # 5列目（インデックス4）がフィルタリング基準
    # check
    print(Z_with_strahler[1, :])
    filtered_Z_by_strahler = Z_with_strahler[Z_with_strahler[:, 5] >= S_min]

    # ストラー数の分布
    unique_strahler, counts = np.unique(strahler_numbers, return_counts=True)
    print("\n--- ストラー数の分布 ---")
    for s_num, count in zip(unique_strahler, counts):
        print(f"ストラー数 {int(s_num)}: {count} 本の枝")
    print("\n--- フィルタリング結果 ---")
    print(f"元のZ行列の行数: {Z_matrix.shape[0]}")
    print(f"ストラー数 >= {S_min} の行数: {filtered_Z_by_strahler.shape[0]}")


    # ----------------------------------------------------
    #

    # インデックスのマッピング

    node_id_map = {}
    current_id = 0
    leaves = get_leaves(filtered_Z_by_strahler)
    print(f"Leaves: {len(leaves)}")

    for leaf in leaves:
        node_id_map[int(leaf)] = current_id
        current_id += 1
    print(f"Number of leaves: {len(leaves)}")

    for row in filtered_Z_by_strahler:
        parent_id = row[2]
        if parent_id not in node_id_map:
            node_id_map[parent_id] = current_id
            current_id += 1
    print(f"Total Node ID Map Size: {len(node_id_map)}")
    print(f"current_id: {current_id}")

    linkage_matrix_mapped_strahler = [ 
        [node_id_map[row[0]], node_id_map[row[1]], node_id_map[row[2]], row[3], strahler_numbers[i]] 
        for i, row in enumerate(filtered_Z_by_strahler)
    ]
    return np.array(linkage_matrix_mapped_strahler), node_id_map


import plotly.express as px
from sklearn.preprocessing import normalize
import umap
def run_hdbscan(X, 
                y, 
                min_samples=25, 
                min_cluster_size=5, 
                max_cluster_size=1000,
                n_neighbors=100, 
                min_dist=1e-3, 
                spread=2.0, 
                n_epochs=500):
    X = normalize(X)
    hdbscan_model = hdbscan.HDBSCAN(
        min_samples=min_samples,
        min_cluster_size=min_cluster_size,
        max_cluster_size=max_cluster_size,
        cluster_selection_method='leaf'
    )
    labels = hdbscan_model.fit_predict(X)
    hdbscan_model.condensed_tree_.plot(select_clusters=True, label_clusters=True, log_size=True, max_rectangles_per_icicle=10)
    umap_model = umap.UMAP(
        n_neighbors=n_neighbors,
        min_dist=min_dist,
        spread=spread,
        n_epochs=n_epochs,
        random_state=42
    )
    embeddings = umap_model.fit_transform(X)

    print(f"クラスタ数: {len(np.unique(labels))}")
    print(f"ノイズ割合: {np.mean(labels == -1):.2%}")

    df = {
        'x': embeddings[:, 0],
        'y': embeddings[:, 1],
        'label': labels.astype(str),
        'index': list(range(len(X)))
    }

    fig = px.scatter(
        df,
        x='x',
        y='y',
        color='label',
        title='HDBSCAN + UMAP クラスタリング可視化',
        color_continuous_scale='Viridis',
        opacity=0.7,
        text='index',
        hover_name=y
    )
    fig.update_traces(marker=dict(size=3))
    fig.update_layout(width=800, height=800)
    fig.show()

    # numpyであればyはastype(str)
    if not isinstance(y, list):
        y = y.astype(str)

    # 実際のラベルの可視化
    if len(np.unique(y)) <= 20:
        fig = px.scatter(
            x=embeddings[:, 0],
            y=embeddings[:, 1],
            color=y,
            title='実際のラベルの可視化',
            color_continuous_scale='Viridis',
            opacity=0.7,
            text=df['index']
            
        )
    else:
        fig = px.scatter(
            x=embeddings[:, 0],
            y=embeddings[:, 1],
            title='実際のラベルの可視化',
            opacity=0.7,
            text=df['index'],
            hover_name=y
        )
    fig.update_traces(marker=dict(size=3))
    fig.update_layout(width=800, height=800)
    fig.show()

    

    # ===== ヒストグラム計算 =====
    unique_labels = np.unique(labels)
    counts = np.array([np.sum(labels == l) for l in unique_labels])

    # ===== Plotlyで可視化 =====
    fig = go.Figure()

    fig.add_trace(go.Bar(
        x=unique_labels,
        y=counts,
        marker_color='blue',
        name='Cluster Size'
    ))

    fig.update_layout(
        title='HDBSCAN Cluster Size Distribution',
        xaxis_title='Cluster Label',
        yaxis_title='Number of Points',
        template='plotly_white'
    )

    fig.show()

    print("\n===== 各クラスタの上位単語を表示（最初の10個） =====")
    # ===== 各クラスタの上位単語を表示（最初の10個） =====
    
    for c in range(0, len(np.unique(labels))):
        # labels == c のインデックスを取得
        indices = np.where(labels == c)[0][:10]  # 上位10個
        words = [y[i] for i in indices]
        print(f"Cluster: {c}, {words}")

    print("\n===== 各クラスタの上位単語をHDBSCANの確率でソートして表示 =====")
    # ===== 各クラスタをHDBSCANの確率でソートして表示 =====
    for c in range(0, 25):
        indices = np.where(labels == c)[0]
        # ラベル内の確率で降順ソート
        indices_sorted = sorted(indices, key=lambda x: 1 - hdbscan_model.probabilities_[x])
        words = [y[i] for i in indices_sorted[:10]]  # 上位10個
        print(f"Cluster: {c}, {words}")

    return hdbscan_model


In [26]:
def run_experiment(condensed_tree, S_list=[2,3,4,5]):
    linkage_matrix, node_id_map1 = get_linkage_matrix_from_hdbscan(condensed_tree)
    segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
    plot_dendrogram_plotly(segments)

    for S_min in S_list:
        print(f"\n--- ストラー数 S_min = {S_min} でフィルタリング ---")
        filtered_linkage_matrix, node_id_map2 = filter_linkage_matrix_by_strahler(linkage_matrix, S_min=S_min, N_leaves=len(_get_leaves(condensed_tree._raw_tree)))
        segments_filtered = get_dendrogram_segments(filtered_linkage_matrix[:, [0,1,3,4]])
        plot_dendrogram_plotly(segments_filtered).show()

In [27]:
%run ../utils-notebook/imports.py

In [28]:
from plotly.colors import sequential

COLOR_SCALE = sequential.Viridis # https://plotly.com/python/builtin-colorscales/
def map_score_to_color(score, min_score, max_score, color_scale):
    # スコアを0-1に正規化
    normalized = (min(max_score, score) - min_score) / (max_score - min_score)
    # カラースケールのインデックスを計算
    index = int(normalized * (len(color_scale) - 1))
    return color_scale[index]


def map_score_to_color_log(score, min_score, max_score, color_scale, epsilon=1e-8):
    # 1. スコアと min/max スコアに対数変換を適用
    #    ゼロ割を避けるため、微小な値 epsilon を加算
    log_score = np.log(score + epsilon)
    log_min = np.log(min_score + epsilon)
    log_max = np.log(max_score + epsilon)
    
    # 2. 対数スコアを 0-1 に正規化 (クリッピング処理を含む)
    #    スコアが範囲外になる場合も考慮
    if log_max == log_min:
        normalized = 0.0 # 分母がゼロの場合
    else:
        # スコアを min/max の範囲にクリッピング
        clipped_log_score = min(log_max, max(log_min, log_score))
        normalized = (clipped_log_score - log_min) / (log_max - log_min)

    # fig = px.histogram(
    #     x=log_score,
    #     nbins=50,
    #     title='Log-Transformed Score Distribution',
    #     labels={'x': 'Log-Transformed Score', 'y': 'Count'},
    #     template='plotly_white'
    # ).show()
        
    # 3. カラースケールのインデックスを計算
    index = int(normalized * (len(color_scale) - 1))
    
    # 範囲外のインデックスにならないよう念のためクリッピング
    index = min(len(color_scale) - 1, max(0, index))
    
    return color_scale[index]

# a

In [29]:
def compute_stability_python(condensed_tree):

    # 1. 最小クラスタとクラスタ数を定義 (Cythonと同じロジック)
    smallest_cluster = condensed_tree['parent'].min()
    num_clusters = condensed_tree['parent'].max() - smallest_cluster + 1
    
    largest_child = max(condensed_tree['child'].max(), smallest_cluster)

    # 2. lambda_birth の計算 (クラスタの誕生時の最小 lambda)
    # condensed_tree を 'child' でソート
    sorted_child_data = np.sort(condensed_tree[['child', 'lambda_val']], axis=0)
    
    # births_arr は、child ID に対応する lambda_birth を保持する
    births_arr = np.nan * np.ones(largest_child + 1, dtype=np.double)
    
    current_child = -1
    min_lambda = 0

    # NumPyの structured array を Pythonループで処理 (Cythonの loopを模倣)
    for row in range(sorted_child_data.shape[0]):
        child = sorted_child_data[row]['child']
        lambda_ = sorted_child_data[row]['lambda_val']

        if child == current_child:
            min_lambda = min(min_lambda, lambda_)
        elif current_child != -1:
            births_arr[current_child] = min_lambda
            current_child = child
            min_lambda = lambda_
        else:
            # Initialize
            current_child = child
            min_lambda = lambda_

    if current_child != -1:
        births_arr[current_child] = min_lambda
        
    births_arr[smallest_cluster] = 0.0 # ルートクラスタの lambda_birth は 0
    
    # 3. Stability スコアの計算
    
    # NumPyのベクトル演算で高速化可能だが、Cythonを模倣しループで計算
    result_arr = np.zeros(num_clusters, dtype=np.double)
    
    parents = condensed_tree['parent']
    sizes = condensed_tree['child_size']
    lambdas = condensed_tree['lambda_val']

    for i in range(condensed_tree.shape[0]):
        parent = parents[i]
        lambda_ = lambdas[i]
        child_size = sizes[i]
        result_index = parent - smallest_cluster
        
        # Stability(C) = Σ (lambda_death - lambda_birth) * size
        # condensed_treeの各行は、parent が child_size のクラスタを 'lambda_' で吸収/結合するステップを示す
        # この lambda_ は、HDBSCANロジックでは lambda_death と見なされる
        
        lambda_birth = births_arr[parent]
        
        # NOTE: HDBSCANのStability定義は複雑なため、ここはHDBSCANの内部ロジックを正確に模倣する必要があります。
        # オリジナルのCythonコードを再現:
        result_arr[result_index] += (lambda_ - lambda_birth) * child_size
        
    # 4. ID とスコアを辞書に変換
    node_ids = np.arange(smallest_cluster, condensed_tree['parent'].max() + 1)
    result_pre_dict = np.vstack((node_ids, result_arr)).T

    # フィルタリングされていないノードを含むため、dictに変換してIDとスコアを対応させる
    # [ID, Score] のペアの配列を辞書に変換
    return dict(zip(result_pre_dict[:, 0].astype(int), result_pre_dict[:, 1]))

In [30]:
import pickle
file_path = "../18_rapids/result/20251030_190647/condensed_tree_object.pkl"
with open(file_path, 'rb') as f:
    condensed_tree = pickle.load(f)

In [4]:
stability_dict = compute_stability_python(condensed_tree._raw_tree)

In [6]:
linkage_matrix, node_id_map1 = get_linkage_matrix_from_hdbscan(condensed_tree)
# dictを逆にする
node_id_map1_reversed = {v: k for k, v in node_id_map1.items()}
scores = [stability_dict[node_id_map1_reversed[int(row[2])]] for row in linkage_matrix] # parent id -> stability score
print(scores[:10])

len of sorted condensed tree: 1890
len of linkage matrix: 945
1890
Number of leaves: 946
Leaf ID Map Size: 946
current id: 946
Total Node ID Map Size: 1891
current_id: 1891
Max Lambda: 4.034491062164307


NameError: name 'stability_dict' is not defined

In [ ]:
# 
denoised_stability = [score for score in stability_dict.values() if score < 600]
fig = px.histogram(
    x=denoised_stability,
    nbins=100,
    title='Stability Score Distribution',
    labels={'x': 'Stability Score', 'y': 'Count'},
    template='plotly_white'
).show()

In [7]:
# サイズでスケーリング
scaled_stability = np.array(scores) / np.array(linkage_matrix[:,4])
fig = px.histogram(
    x=scaled_stability,
    nbins=100,
    title='Scaled Stability Score Distribution',
    labels={'x': 'Scaled Stability Score', 'y': 'Count'},
    template='plotly_white'
).show()

In [11]:
# color
scores = scaled_stability.tolist()
max_score = max(scores)
min_score = min(scores)

colors = [map_score_to_color_log(score, min_score, max_score, COLOR_SCALE) for score in scores]



NameError: name 'scaled_stability' is not defined

In [61]:
colors = sum([[color]*3 for color in colors], [])
scores = sum([[score]*3 for score in scores], [])
print(len(colors), len(scores))


516 516


In [58]:
import plotly.express as px
import numpy as np

# 1. 0から100までの連続した値を1行のデータとして作成
#    （カラースケールがどのように適用されるかを見るためのダミーデータ）
data = np.arange(100).reshape(1, 100)

# 2. imshow (ヒートマップ) を使用し、カラーマップを適用
fig = px.imshow(
    data, 
    color_continuous_scale='Viridis', # ここに表示したいカラースケールの名前を指定
    aspect="auto",
    title='Continuous Color Scale: Viridis',
    height=300,
    width=500
)

# 軸の情報を非表示にする
fig.update_xaxes(showticklabels=False)
fig.update_yaxes(showticklabels=False)
# fig.update_layout(height=100, width=500)
fig.show()

In [62]:
segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show()
# colorscale fig


In [83]:
segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show()

### 500000

In [31]:
import pickle
file_path = "../18_rapids/result/20251030_185048/condensed_tree_object.pkl"
with open(file_path, 'rb') as f:
    condensed_tree = pickle.load(f)

#### stability

In [32]:
stability_dict = compute_stability_python(condensed_tree._raw_tree)
linkage_matrix, node_id_map1 = get_linkage_matrix_from_hdbscan(condensed_tree)
# dictを逆にする
node_id_map1_reversed = {v: k for k, v in node_id_map1.items()}
scores = np.array([stability_dict[node_id_map1_reversed[int(row[2])]] for row in linkage_matrix])

# scaled by size
# scores = (np.array(scores) / np.array(linkage_matrix[:,4].astype(float))).tolist()

# color 
# max: 5%を除いたときのmax
def max_after_clipping_top(arr, percentage_to_exclude=5):
    """
    NumPy配列の上位Nパーセントの値を除外した後の最大値を計算する。

    Args:
        arr (np.ndarray): 入力NumPy配列。
        percentage_to_exclude (int/float): 除外したい上位のパーセンテージ（例: 5）。

    Returns:
        float: 外れ値を除外した後の最大値。
    """
    
    # 95パーセンタイル (P_95) の値を計算 (上位5%を除外)
    # P_95 は、データ全体の95%がこの値以下であることを意味する。
    percentile_value = 100 - percentage_to_exclude
    threshold = np.percentile(arr, percentile_value)
    
    # 閾値以下の要素だけを抽出してフィルタリング
    filtered_arr = arr[arr <= threshold]
    
    if filtered_arr.size == 0:
        # すべての値が除外される稀なケース（例: 入力配列が非常に小さい場合）
        return np.nan
    
    # フィルタリングされた配列の最大値を返す
    clipped_max = np.max(filtered_arr)
    
    return clipped_max
max_score = max_after_clipping_top(np.array(scores), percentage_to_exclude=5)
min_score = min(scores)
print(f"Max Score: {max_score}, Min Score: {min_score}")
fig = px.histogram(
    x=scores[scores < max_score],
    nbins=100,
    title='Stability Score Distribution',
    labels={'x': 'Stability Score', 'y': 'Count'},
    template='plotly_white'
).show()
colors = [map_score_to_color(score, min_score, max_score, COLOR_SCALE) for score in scores]
colors = sum([[color]*3 for color in colors], [])
scores = sum([[score]*3 for score in scores], [])
print(len(colors), len(scores))
print(linkage_matrix.shape)
print(linkage_matrix[:, 4].dtype)
segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show()


len of sorted condensed tree: 1890
len of linkage matrix: 945
1890
Number of leaves: 946
Leaf ID Map Size: 946
current id: 946
Total Node ID Map Size: 1891
current_id: 1891
Max Lambda: 4.034491062164307
Max Score: 245.0119183063507, Min Score: 0.0


2835 2835
(945, 5)
float64


In [18]:
stability_dict = compute_stability_python(condensed_tree._raw_tree)
linkage_matrix, node_id_map1 = get_linkage_matrix_from_hdbscan(condensed_tree)
# dictを逆にする
node_id_map1_reversed = {v: k for k, v in node_id_map1.items()}

# size 
scores = linkage_matrix[:,4].astype(float).tolist()

# scaled by size
# scores = (np.array(scores) / np.array(linkage_matrix[:,4].astype(float))).tolist()

# color
max_score = max(scores)
min_score = min(scores)
print(f"Max Score: {max_score}, Min Score: {min_score}")
colors = [map_score_to_color_log(score, min_score, max_score, COLOR_SCALE) for score in scores]
colors = sum([[color]*3 for color in colors], [])
scores = sum([[score]*3 for score in scores], [])
print(len(colors), len(scores))

fig = px.histogram(
    x=scores,
    nbins=100,
    title='Linkage Size Score Distribution',
    labels={'x': 'Linkage Size Score', 'y': 'Count'},
    template='plotly_white'
).show()

segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show()


len of sorted condensed tree: 1890
len of linkage matrix: 945
1890
Number of leaves: 946
Leaf ID Map Size: 946
current id: 946
Total Node ID Map Size: 1891
current_id: 1891
Max Lambda: 4.034491062164307
Max Score: 493411.0, Min Score: 13.0
2835 2835


### いろいろ

#### Strahler

In [35]:
def calculate_strahler(Z_matrix: np.ndarray, n_leaves: int) -> np.ndarray:
    """
    Linkage Matrix (Z) に基づいて、各結合ノードのストラー数（Strahler Number）を計算する。
    
    Args:
        Z_matrix: Linkage Matrix (N-1 x 4のNumPy配列)。
        n_leaves: 元の観測値/葉ノードの数。
        
    Returns:
        np.ndarray: 各結合ノード（Zの各行）に対応するストラー数の配列。
    """
    n_merges = Z_matrix.shape[0]
    
    # 葉ノードのストラー数を初期化 (すべての葉ノードは S=1)
    # インデックス: 0から n_leaves - 1
    strahler_map = {i: 1 for i in range(n_leaves)}
    
    # Zの各行に対応するストラー数を格納するリスト
    merge_strahler_numbers = np.zeros(n_merges, dtype=int)
    
    # Z行列をボトムアップ（行 0 から N-2）で処理
    for i in range(n_merges):
        u_idx = int(Z_matrix[i, 0])  # 結合されるノード u
        v_idx = int(Z_matrix[i, 1])  # 結合されるノード v
        new_idx = n_leaves + i       # 新しく生成されるノード
        
        # 子ノードのストラー数を取得
        s_u = strahler_map.get(u_idx, 1)
        s_v = strahler_map.get(v_idx, 1)
        
        # ストラー数計算ロジック（二分木）
        # if s_u == s_v:
        #     # S_u = S_v の場合、新しいノードのストラー数は S_u + 1
        #     s_new = s_u + 1
        # else:
        #     # S_u != S_v の場合、新しいノードのストラー数は Max(S_u, S_v)
        #     s_new = max(s_u, s_v)
        s_new = max(s_u, s_v) + min(s_u, s_v) / max(s_u, s_v)
        
        # 結果を記録し、マップを更新
        merge_strahler_numbers[i] = s_new
        strahler_map[new_idx] = s_new

    return merge_strahler_numbers


In [36]:
stability_dict = compute_stability_python(condensed_tree._raw_tree)
linkage_matrix, node_id_map1 = get_linkage_matrix_from_hdbscan(condensed_tree)
# dictを逆にする
node_id_map1_reversed = {v: k for k, v in node_id_map1.items()}

# size 
scores = calculate_strahler(linkage_matrix, n_leaves=len(_get_leaves(condensed_tree._raw_tree))).tolist()
print(f"scores length: {len(scores)}")

# scaled by size
# scores = (np.array(scores) / np.array(linkage_matrix[:,4].astype(float))).tolist()

# color
max_score = max(scores)
min_score = min(scores)
print(f"Max Score: {max_score}, Min Score: {min_score}")
colors = [map_score_to_color_log(score, min_score, max_score, COLOR_SCALE) for score in scores]
colors = sum([[color]*3 for color in colors], [])
scores = sum([[score]*3 for score in scores], [])
print(len(colors), len(scores))

fig = px.histogram(
    x=scores,
    nbins=100,
    title='Linkage Size Score Distribution',
    labels={'x': 'Linkage Size Score', 'y': 'Count'},
    template='plotly_white'
).show()

segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show()

len of sorted condensed tree: 1890
len of linkage matrix: 945
1890
Number of leaves: 946
Leaf ID Map Size: 946
current id: 946
Total Node ID Map Size: 1891
current_id: 1891
Max Lambda: 4.034491062164307
1890
scores length: 945
Max Score: 42, Min Score: 2
2835 2835


#### Custom strahler

In [ ]:
import numpy as np

def calculate_custom_strahler(Z, num_original_nodes, S_initial_scores):
    """
    scipyの連結行列 Z を処理し、子ノードの安定度（または既に計算されたバランススコア）
    に基づいて新しい親ノードの安定度バランススコアを計算する。
    
    Args:
        Z (np.ndarray): 連結行列 (shape: (n-1, 4))。
        num_original_nodes (int): 元のデータポイントの数 n。
        S_initial_scores (dict): リーフノード（HDBSCANの安定クラスタ）の初期安定度スコア。
        
    Returns:
        dict: 各ノードIDに対応する最終的なバランススコア（累積）。
    """
    
    # 1. 各ノードの現在のスコアを格納する辞書を初期化
    #    最初は初期安定度スコアで埋める
    current_scores_map = S_initial_scores.copy() 
    
    # Z行列の行インデックス i から parent_id を計算
    
    for i, row in enumerate(Z):
        u_id = int(row[0]) 
        v_id = int(row[1]) 
        parent_id = num_original_nodes + i
        
        # ----------------------------------------------------
        # スコアの取得
        # ----------------------------------------------------
        
        # 子ノードのスコアを取得。
        # S_u, S_v には、初期安定度、または既に計算された親ノードのバランススコアが入る。
        S_u = current_scores_map.get(u_id, 0.0) 
        S_v = current_scores_map.get(v_id, 0.0)
        
        # ----------------------------------------------------
        # 新しい親ノードのスコア S_new の計算
        # ----------------------------------------------------
        # print(f"Processing parent_id: {parent_id}, child_ids: ({u_id}, {v_id}), scores: ({S_u}, {S_v})")
        if S_u == 0.0 and S_v == 0.0:
            S_new = 1.0 
        elif S_u == 0.0 or S_v == 0.0:
            S_new = 0.0
        else:
            # 安定度バランスの計算ロジック
            S_new = min(S_u, S_v) / max(S_u, S_v)
        
        # 2. 親ノードのスコアを更新
        #    これが、次の結合イベントで子ノードのスコアとして使われる
        current_scores_map[parent_id] = S_new
        
    # 最終的なスコアマップを返す
    return current_scores_map

# --- 使用上の注意 ---
# S_initial_scores には、HDBSCANで安定クラスタとされたノードIDと、
# それに対応する HDBSCAN安定度スコア（S）が格納されている必要があります。
# リーフノード（データポイント）のIDは含めず、安定クラスタのIDのみで開始するのが一般的です。

In [44]:
score_dict = calculate_custom_strahler(
    Z=linkage_matrix,
    num_original_nodes=len(_get_leaves(condensed_tree._raw_tree)),
    S_initial_scores={node_id_map1_reversed[k]: v for k, v in stability_dict.items() if k in node_id_map1_reversed}
)

1890
Processing parent_id: 946, child_ids: (361, 362), scores: (0.0, 0.0)
Processing parent_id: 947, child_ids: (324, 325), scores: (0.0, 0.0)
Processing parent_id: 948, child_ids: (946, 363), scores: (1.0, 0.0)
Processing parent_id: 949, child_ids: (377, 378), scores: (0.0, 0.0)
Processing parent_id: 950, child_ids: (368, 369), scores: (0.0, 0.0)
Processing parent_id: 951, child_ids: (381, 382), scores: (0.0, 0.0)
Processing parent_id: 952, child_ids: (948, 364), scores: (0.0, 0.0)
Processing parent_id: 953, child_ids: (365, 366), scores: (0.0, 0.0)
Processing parent_id: 954, child_ids: (405, 406), scores: (0.0, 0.0)
Processing parent_id: 955, child_ids: (374, 375), scores: (0.0, 0.0)
Processing parent_id: 956, child_ids: (376, 949), scores: (0.0, 1.0)
Processing parent_id: 957, child_ids: (955, 956), scores: (1.0, 0.0)
Processing parent_id: 958, child_ids: (373, 957), scores: (0.0, 0.0)
Processing parent_id: 959, child_ids: (371, 372), scores: (0.0, 0.0)
Processing parent_id: 960, ch

In [45]:
score_map = calculate_custom_strahler(linkage_matrix,len(_get_leaves(condensed_tree._raw_tree)),score_dict)

1890
Processing parent_id: 946, child_ids: (361, 362), scores: (0.0, 0.0)
Processing parent_id: 947, child_ids: (324, 325), scores: (0.0, 0.0)
Processing parent_id: 948, child_ids: (946, 363), scores: (1.0, 0.0)
Processing parent_id: 949, child_ids: (377, 378), scores: (0.0, 0.0)
Processing parent_id: 950, child_ids: (368, 369), scores: (0.0, 0.0)
Processing parent_id: 951, child_ids: (381, 382), scores: (0.0, 0.0)
Processing parent_id: 952, child_ids: (948, 364), scores: (0.0, 0.0)
Processing parent_id: 953, child_ids: (365, 366), scores: (0.0, 0.0)
Processing parent_id: 954, child_ids: (405, 406), scores: (0.0, 0.0)
Processing parent_id: 955, child_ids: (374, 375), scores: (0.0, 0.0)
Processing parent_id: 956, child_ids: (376, 949), scores: (0.0, 1.0)
Processing parent_id: 957, child_ids: (955, 956), scores: (1.0, 0.0)
Processing parent_id: 958, child_ids: (373, 957), scores: (0.0, 0.0)
Processing parent_id: 959, child_ids: (371, 372), scores: (0.0, 0.0)
Processing parent_id: 960, ch

In [46]:
scores = [score_map[int(row[2])] for row in linkage_matrix]

max_score = max(scores)
min_score = min(scores)
colors = [map_score_to_color_log(score, min_score, max_score, COLOR_SCALE) for score in scores]
colors = sum([[color]*3 for color in colors], [])
scores = sum([[score]*3 for score in scores], [])
print(len(colors), len(scores))
segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show()

2835 2835


#### Stability change

In [37]:
# 親子と比較したときのStabilityの変化

def calculate_stability_change(Z_matrix: np.ndarray, stability_dict: dict) -> np.ndarray:
    """
    Linkage Matrix (Z) に基づいて、各結合ノードのStability変化を計算する。
    
    Args:
        Z_matrix: Linkage Matrix (N-1 x 4のNumPy配列)。
        stability_dict: 各ノードIDに対応するStabilityスコアの辞書。
    """
    n_merges = Z_matrix.shape[0]
    
    stability_changes = np.zeros(n_merges, dtype=float)
    
    for i in range(n_merges):
        u_idx = int(Z_matrix[i, 0])  # 結合されるノード u
        v_idx = int(Z_matrix[i, 1])  # 結合されるノード v
        parent_idx = int(Z_matrix[i, 2])  # 新しく生成されるノード
        
        S_u = stability_dict.get(u_idx, 0.0)
        S_v = stability_dict.get(v_idx, 0.0)
        S_parent = stability_dict.get(parent_idx, 0.0)
        
        # Stability変化の計算
        stability_changes[i] = S_parent - (S_u + S_v)

    return stability_changes


In [49]:
# indexがずれているので、node_id_map1_reversedを使って変換
score_dict = {node_id_map1_reversed[k]: v for k, v in stability_dict.items() if k in node_id_map1_reversed}
# S_initial_scores={node_id_map1_reversed[k]: v for k, v in stability_dict.items() if k in node_id_map1_reversed}

stability_change = calculate_stability_change(linkage_matrix, score_dict)
print(stability_change[:10])

[0. 0. 0. 0. 0. 0. 0. 0. 0. 0.]


In [48]:
scores = stability_change.tolist()
fig = px.histogram(
    x=scores,
    nbins=100,
    title='Stability Change Score Distribution',
    labels={'x': 'Stability Change Score', 'y': 'Count'},
    template='plotly_white'
).show(renderer="browser")
max_score = max(scores)
min_score = min(scores)
colors = [map_score_to_color_log(score, min_score, max_score, COLOR_SCALE) for score in scores]
colors = sum([[color]*3 for color in colors], [])
scores = sum([[score]*3 for score in scores], [])
print(len(colors), len(scores))
segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show(renderer="browser")

2835 2835


#### 合併比率

In [50]:
# クラスタサイズの合併比率
def calculate_merge_size_ratio(Z_matrix: np.ndarray) -> np.ndarray:
    """
    Linkage Matrix (Z) に基づいて、各結合ノードのクラスタサイズの合併比率を計算する。
    
    Args:
        Z_matrix: Linkage Matrix (N-1 x 4のNumPy配列)。
        
    Returns:
        np.ndarray: 各結合ノード（Zの各行）に対応するクラスタサイズの合併比率の配列。
    """
    n_merges = Z_matrix.shape[0]
    
    merge_size_ratios = np.zeros(n_merges, dtype=float)
    
    for i in range(n_merges):
        u_idx = int(Z_matrix[i, 0])  # 結合されるノード u
        v_idx = int(Z_matrix[i, 1])  # 結合されるノード v
        count_u = Z_matrix[i, 3] if u_idx < Z_matrix.shape[0] else Z_matrix[int(u_idx - Z_matrix.shape[0]), 3]
        count_v = Z_matrix[i, 3] if v_idx < Z_matrix.shape[0] else Z_matrix[int(v_idx - Z_matrix.shape[0]), 3]
        
        # クラスタサイズの合併比率の計算
        smaller_size = min(count_u, count_v)
        larger_size = max(count_u, count_v)
        merge_size_ratios[i] = smaller_size / larger_size if larger_size > 0 else 0.0

    return merge_size_ratios




In [52]:
scores = calculate_merge_size_ratio(linkage_matrix)

fig = px.histogram(
    x=scores,
    nbins=100,
    title='Stability Change Score Distribution',
    labels={'x': 'Stability Change Score', 'y': 'Count'},
    template='plotly_white'
).show(renderer="browser")
max_score = max(scores)
min_score = min(scores)
colors = [map_score_to_color(score, min_score, max_score, COLOR_SCALE) for score in scores]
colors = sum([[color]*3 for color in colors], [])
scores = sum([[score]*3 for score in scores], [])
print(len(colors), len(scores))
segments = get_dendrogram_segments(linkage_matrix[:, [0,1,3,4]])
fig = plot_dendrogram_plotly(segments, colors=colors, scores=scores)
fig.update_layout(height=1000)
fig.show(renderer="browser")

2835 2835


In [53]:
# scoresが1の数
print(f"Scores == 1.0: {np.sum(np.array(scores) == 1.0)}")

Scores == 1.0: 2208


# dash

In [20]:

from jupyter_dash import JupyterDash # 💡 これがJupyter Notebookで実行するための鍵
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.figure_factory as ff
from scipy.cluster.hierarchy import linkage, fcluster
import numpy as np
import pandas as pd

# # --- 1. データと連結行列 (Z_matrix) の準備 ---
# np.random.seed(42)
# X = np.random.rand(50, 2)
# labels = [f'Point {i}' for i in range(50)]
# Z = linkage(X, method='ward')
# MAX_DISTANCE = Z[:, 2].max()
Z = linkage_matrix
labels = [f'Point {i}' for i in range(linkage_matrix.shape[0] + 1)]
MAX_DISTANCE = 5


# --- 2. Z_matrixからデンドログラム図を生成する関数（変更なし） ---
def create_dendrogram_figure(Z, threshold=0, labels=None):
    print(f"Filtering with Strahler Threshold: {threshold}")
    filtered_Z = filter_linkage_matrix_by_strahler(Z, S_min=threshold, N_leaves=len(labels))[0]

    segments = get_dendrogram_segments(filtered_Z[:, [0,1,3,4]])
    fig = plot_dendrogram_plotly(segments)
    return fig

# --- 3. Dash アプリケーションの定義（修正点） ---
# 💡 dash.Dash の代わりに JupyterDash.JupyterDash を使う
app = JupyterDash(__name__) 

app.layout = html.Div([
    html.H2("Dendrogram Filtering in Jupyter Notebook"),
    
    html.Div([
        html.Label("Clustering Threshold (距離の閾値):"),
        dcc.Slider(
            id='threshold-slider',
            min=0,
            max=MAX_DISTANCE,
            step=MAX_DISTANCE / 100,
            value=0.5 * MAX_DISTANCE, 
            # 修正点: np.float64 を str に変換
            marks={str(i): f'{i:.1f}' for i in np.linspace(0, MAX_DISTANCE, 5)},
            tooltip={"placement": "bottom", "always_visible": True}
        ),
    ], style={'padding': '20px'}),
    
    dcc.Graph(id='dendrogram-output'),
])

# --- 4. コールバック（変更なし） ---
@app.callback(
    Output('dendrogram-output', 'figure'),
    [Input('threshold-slider', 'value')]
)
def update_dendrogram(selected_threshold):
    fig = create_dendrogram_figure(Z, selected_threshold, labels)
    return fig

# --- 5. アプリケーションの実行（修正点） ---
# 💡 app.run_server() の代わりに app.run_server(mode='inline') を使う
app.run_server(mode="external")





Dash is running on http://127.0.0.1:8050/

Dash app running on http://127.0.0.1:8050/


Filtering with Strahler Threshold: 2.5
[3.24000000e+02 3.25000000e+02 9.47000000e+02 2.63478518e-01
 4.00000000e+01 2.00000000e+00]

--- ストラー数の分布 ---
ストラー数 2: 136 本の枝
ストラー数 3: 16 本の枝
ストラー数 4: 793 本の枝

--- フィルタリング結果 ---
元のZ行列の行数: 945
ストラー数 >= 2.5 の行数: 809
root: 1890.0
Filtering with Strahler Threshold: 2.5
[3.24000000e+02 3.25000000e+02 9.47000000e+02 2.63478518e-01
 4.00000000e+01 2.00000000e+00]

--- ストラー数の分布 ---
ストラー数 2: 136 本の枝
ストラー数 3: 16 本の枝
ストラー数 4: 793 本の枝

--- フィルタリング結果 ---
元のZ行列の行数: 945
ストラー数 >= 2.5 の行数: 809
root: 1890.0
Filtering with Strahler Threshold: 2.5
[3.24000000e+02 3.25000000e+02 9.47000000e+02 2.63478518e-01
 4.00000000e+01 2.00000000e+00]

--- ストラー数の分布 ---
ストラー数 2: 136 本の枝
ストラー数 3: 16 本の枝
ストラー数 4: 793 本の枝

--- フィルタリング結果 ---
元のZ行列の行数: 945
ストラー数 >= 2.5 の行数: 809
root: 1890.0
Leaves: 810
Number of leaves: 810
Total Node ID Map Size: 1619
current_id: 1619
Leaves: 810
Number of leaves: 810
Total Node ID Map Size: 1619
current_id: 1619
Leaves: 810
Number of leaves: 810
To